## refs
- https://towardsdatascience.com/dbscan-algorithm-complete-guide-and-application-with-python-scikit-learn-d690cbae4c5d
- https://hdbscan.readthedocs.io/en/latest/comparing_clustering_algorithms.html#
- https://github.com/gboeing/2014-summer-travels/blob/master/clustering-scikitlearn.ipynb

In [1]:
import json
import time # unused?
import csv
import seaborn as sns
import numpy as np # +dep
import pandas as pd # +dep
import matplotlib.pyplot as plt # interactive notebook
#import seaborn as sns # unused?
import matplotlib as mpl
# mappings, interactive notebook
#import cartopy
import folium

In [2]:
# raw NRT data
import pathlib
#data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/fire.csv").resolve()))
data_y2019 = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/hotspots_data_2019.csv").resolve()))
#data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/hotspots_data_2019.csv").resolve()))
#data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/ARIMA-train-day1.csv"...).resolve()))
#data2 = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/ARIMA-train-day2.csv").resolve()))
filtered_data = data_y2019[data_y2019.acq_date.str.contains('2019-03')].append(data_y2019[data_y2019.acq_date.str.contains('2019-04')])
filtered_data.acq_date.unique()
data_y2019.head()

latitude   longitude  bright_ti4  scan  track    acq_date  acq_time  \
0  14.373807  100.632462      326.08  0.34   0.56  2019-01-01       557   
1  14.378959  100.631424      341.67  0.34   0.56  2019-01-01       557   
2  14.624126  102.694824      334.70  0.50   0.49  2019-01-01       557   
3  14.395066  102.168671      328.69  0.54   0.51  2019-01-01       557   
4  14.996263  104.727219      335.78  0.55   0.43  2019-01-01       557   

  satellite instrument confidence  version  bright_ti5   frp  type  
0         N      VIIRS          n        1      281.98  2.49     0  
1         N      VIIRS          n        1      283.59  2.49     0  
2         N      VIIRS          n        1      286.68  4.82     0  
3         N      VIIRS          n        1      288.09  4.43     0  
4         N      VIIRS          n        1      299.92  4.33     0

In [3]:
import math

GRIDS = 100
hotspots_counts = np.zeros((GRIDS,GRIDS))
#กำหนดค่า
pi = math.pi
r_earth = 6371000.0 #m
#กำหนดจุดแรกของ grid ที่จะวาดบนแผนที่
lat = 17.779913 
lon = 97.715363
dy2 = 350
dx2 = 350
lat_step =  (dy2 / r_earth) * (180 / pi)
lon_step =  (dx2 / r_earth) * (180 / pi) / math.cos(lat * pi/180)

#แบ่ง lat lon ออกเป็น 100 ช่อง
lons = np.arange(lon,lon+lon_step*100,lon_step)
lats = np.arange(lat,lat+lat_step*100,lat_step)
print(len(lons))
print(len(lats))
print('sample lat : ',lats[1],lats[2],lats[3])
print('sample lon : ',lons[1],lons[2],lons[3])

101
101
sample lat :  17.783060625620717 17.786208251241433 17.78935587686215
sample lon :  97.7186685082432 97.7219740164864 97.7252795247296


In [4]:
#april_data = pd.read_csv(str(pathlib.Path("/home/jkp/Documents/agni/extras/firem04-m05.csv").resolve()))
april_data = filtered_data
april_data.head()
unique_date = april_data.acq_date.unique()
#unique_date = ['2019-04-01','2019-04-02']
print(unique_date)

['2019-03-01' '2019-03-02' '2019-03-03' '2019-03-04' '2019-03-05'
 '2019-03-06' '2019-03-07' '2019-03-08' '2019-03-09' '2019-03-10'
 '2019-03-11' '2019-03-12' '2019-03-13' '2019-03-14' '2019-03-15'
 '2019-03-16' '2019-03-17' '2019-03-18' '2019-03-19' '2019-03-20'
 '2019-03-21' '2019-03-22' '2019-03-23' '2019-03-24' '2019-03-25'
 '2019-03-26' '2019-03-27' '2019-03-28' '2019-03-29' '2019-03-30'
 '2019-03-31' '2019-04-01' '2019-04-02' '2019-04-03' '2019-04-04'
 '2019-04-05' '2019-04-06' '2019-04-07' '2019-04-08' '2019-04-09'
 '2019-04-10' '2019-04-11' '2019-04-12' '2019-04-13' '2019-04-14'
 '2019-04-15' '2019-04-16' '2019-04-17' '2019-04-18' '2019-04-19'
 '2019-04-20' '2019-04-21' '2019-04-22' '2019-04-23' '2019-04-24'
 '2019-04-25' '2019-04-26' '2019-04-27' '2019-04-28' '2019-04-29'
 '2019-04-30']


In [5]:
count_results = []
GRIDS = len(lats)
for days in unique_date:
    source = april_data
    read_data = source[april_data.acq_date.eq(days)]
    hotspots_counts = np.ones((GRIDS,GRIDS))
    for i,r in read_data.iterrows():
        for b1 in range(GRIDS):
            if lats[b1] - (lat_step/2) <= r['latitude'] < lats[b1] + (lat_step/2):
                for b2 in range(GRIDS):
                    if lons[b2] - (lon_step/2 ) <= r['longitude'] < lons[b2] + (lon_step/2):
                        hotspots_counts[b1,b2] = 2
                        #hotspots_counts[b1,b2] += 1
    count_results.append(hotspots_counts)

In [8]:
neighbourhood = ((-1,-1), (-1,0), (-1,1), (0,-1), (0, 1), (1,-1), (1,0), (1,1))
#ชนิดข้อมูล EMPTY เคยไหม้แล้ว TREE ไม่เคยไหม้ FIRE จุดความร้อน
EMPTY, TREE, FIRE = 0, 1, 2
nx, ny = 100, 100
#colors_list = [(0.2,0,0), (0,0.5,0), (1,0,0), 'orange']
#cmap = colors.ListedColormap(colors_list)
#bounds = [0,1,2,3]
#norm = colors.BoundaryNorm(bounds, cmap.N)
#plt.imshow(count_results[30],origin='lower',cmap=cmap,norm=norm)
#plt.show()

In [27]:
#ฟังชันกระจายจุดความร้อนออกไปช่องรอบๆ
def iterate(X):
    """Iterate the forest according to the forest-fire rules."""
    # The boundary of the forest is always empty, so only consider cells
    # indexed from 1 to nx-2, 1 to ny-2
    nx, ny = 100, 100
    X1 = np.zeros((ny, nx))
    for ix in range(1,nx-1):
        for iy in range(1,ny-1):
            if X[iy,ix] == FIRE:
                X1[iy,ix] = EMPTY
            if X[iy,ix] == TREE:
                X1[iy,ix] = TREE
                for dx,dy in neighbourhood:
                    if X[iy+dy,ix+dx] == FIRE:
                        X1[iy,ix] = FIRE
                        break
    return X1

In [43]:
#ดูว่าไฟช่องไหนไหม้ไปแล้วบ้าง firstIDX วันแรก lastIDX วันสุดท้าย
area = count_results[32]
def markEmptyArea(data,firstIDX,lastIDX):
    empty_lands = np.ones((GRIDS,GRIDS))
    for i in range(firstIDX,lastIDX):
        print(i)
        tmp = data[i]
        for ix in range(1,nx-1):
            for iy in range(1,ny-1):
                #change old fire to empty lands
                if tmp[iy,ix] == FIRE:
                    empty_lands[iy,ix] = EMPTY
    return empty_lands
#มาร์คว่าไฟจะกระจายไปช่องไหนได้บ้าง
def markFire(lands,fire):
    for ix in range(1,nx-1):
        for iy in range(1,ny-1):
            #change old fire to empty lands
            if fire[iy,ix] == FIRE:
                lands[iy,ix] = FIRE
    return lands
#ส่งไปในฟังชันมารค์จุดที่เคยเกิดไฟ
start_date = 21
end_date = 35
markedEmpty = markEmptyArea(count_results,start_date,end_date) #count results มี 61 วันเลือกมาร์คช่องที่เกิดไฟแล้วในวันที่ 21 ถึง 35
#กระจายไฟออกรอบๆ
markedFire = markFire(markedEmpty,count_results[35])

21
22
23
24
25
26
27
28
29
30
31
32
33
34


In [32]:
#กระจายไฟที่อาจจะมีในวัดถัดไป
nextDayFire = iterate(markedFire)

In [50]:
import pyproj
import math
CELLTYPE = ['EMPTY', 'TREE', 'FIRE']
#source https://stackoverflow.com/questions/7477003/calculating-new-longitude-latitude-from-old-n-meters
#กำหนดจุดศูนย์กลางของ grid แรก
lat = 17.779913 
lon =  97.715363

pi = math.pi
r_earth = 6371000.0 #m
lmap = folium.Map(location=[lat, lon], zoom_start=15)
dy2 = 350/2
dx2 = 350/2
step_lat =  (dy2 / r_earth) * (180 / pi)
step_lon =  (dx2 / r_earth) * (180 / pi) / math.cos(lat * pi/180)

#more grid
target = nextDayFire
start_lon = lon
curr_lat = lat
curr_lon  = start_lon
draw_b1=0
#to influx
predict_points = []


for ix in range(0,GRIDS):
    draw_b2 = 0
    for iy in range(0,GRIDS):
        points = [(curr_lat-step_lat,curr_lon-step_lon),(curr_lat+step_lat,curr_lon+step_lon)]
        #save data
        if target[ix,iy] != TREE:
            save_dict = {
                    'latitude' : lat + step_lat*2*ix,
                    'longitude' : lon + step_lon*2*iy,
                    'base_date' : unique_date[end_date],
                    'type': CELLTYPE[int(target[ix,iy])]
            }
            predict_points.append(save_dict)
          
    draw_b1+=1
    curr_lat += step_lat*2
    curr_lon = start_lon

#plot data
data = data_y2019[data_y2019.acq_date.str.contains('2019-04-06')]
for _, row in data.iterrows():
    folium.CircleMarker(location=(row['latitude'], row['longitude']),
                        radius=6, fill_color='red', fill_opacity=1,
                        popup="<b>lat</b>: {} <b>lon</b>: {}".format(row['latitude'],row['longitude'])
                        ).add_to(lmap)
    points = [(row['latitude']-step_lat,row['longitude']-step_lon),(row['latitude']+step_lat,row['longitude']+step_lon)]
    #folium.Rectangle(bounds=points,fill=False,color = 'red',weight=1).add_to(lmap)
lmap

In [52]:
target = nextDayFire
start_lon = lon
curr_lat = lat
curr_lon  = start_lon
draw_b1=0
for ix in range(0,GRIDS):
    draw_b2 = 0
    for iy in range(0,GRIDS):
        points = [(curr_lat-step_lat,curr_lon-step_lon),(curr_lat+step_lat,curr_lon+step_lon)]
        if target[ix,iy] == FIRE:
            print('Fire',ix,iy)
        elif target[ix,iy] == TREE:
            opa = 0.5
            #folium.Rectangle(bounds=points,fill=True,color = 'black',fill_color = 'green',fill_opacity=opa,weight=1).add_to(lmap)
        
        draw_b2+=1
        curr_lon += step_lon*2
        
    draw_b1+=1
    curr_lat += step_lat*2
    curr_lon = start_lon

Fire 1 60
Fire 1 61
Fire 1 62
Fire 1 64
Fire 2 60
Fire 2 62
Fire 2 63
Fire 2 64
Fire 3 60
Fire 3 61
Fire 3 62
Fire 19 28
Fire 19 29
Fire 19 30
Fire 19 31
Fire 20 27
Fire 20 28
Fire 20 31
Fire 21 27
Fire 21 29
Fire 21 30
Fire 21 31
Fire 22 27
Fire 22 28
Fire 22 29
Fire 24 59
Fire 24 60
Fire 24 61
Fire 25 57
Fire 25 58
Fire 25 59
Fire 25 61
Fire 26 57
Fire 26 61
Fire 27 57
Fire 27 58
Fire 27 59
Fire 27 60
Fire 27 61
Fire 28 66
Fire 28 67
Fire 28 68
Fire 29 66
Fire 29 68
Fire 29 69
Fire 30 66
Fire 30 67
Fire 30 69
Fire 30 70
Fire 31 63
Fire 31 64
Fire 31 65
Fire 31 66
Fire 31 68
Fire 31 70
Fire 32 63
Fire 32 67
Fire 32 68
Fire 32 69
Fire 32 70
Fire 32 71
Fire 32 72
Fire 32 73
Fire 33 63
Fire 33 64
Fire 33 65
Fire 33 66
Fire 33 71
Fire 33 73
Fire 33 75
Fire 34 71
Fire 34 72
Fire 34 75
Fire 35 70
Fire 35 72
Fire 35 73
Fire 35 75
Fire 36 72
Fire 37 70
Fire 37 71
Fire 37 72
Fire 39 71
Fire 39 72
Fire 40 42
Fire 40 43
Fire 40 44
Fire 40 45
Fire 40 70
Fire 41 42
Fire 41 45
Fire 42 42
Fire 42 43

In [44]:
unique_date[end_date]

'2019-04-05'

In [51]:
predict_points

[{'latitude': 17.779913,
  'longitude': 97.715363,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.7186685082432,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.7219740164864,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.7252795247296,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.72858503297282,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.73189054121602,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.73519604945922,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.73850155770242,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude': 97.74180706594562,
  'base_date': '2019-04-05',
  'type': 'EMPTY'},
 {'latitude': 17.779913,
  'longitude':

In [9]:
#source https://stackoverflow.com/questions/7477003/calculating-new-longitude-latitude-from-old-n-meters
lat = 17.779913 
lon = 97.715363

pi = math.pi
r_earth = 6371000.0 #m
lmap = folium.Map(location=[lat, lon], zoom_start=15)
dy2 = 350/2
dx2 = 350/2
step_lat =  (dy2 / r_earth) * (180 / pi)
step_lon =  (dx2 / r_earth) * (180 / pi) / math.cos(lat * pi/180)

#draw one grid
points = [(lat-step_lat,lon-step_lon),(lat+step_lat,lon+step_lon)]
folium.Rectangle(bounds=points,fill=True,color = 'red',fill_color = '#940091',fill_opacity=0,weight=1).add_to(lmap)

#more grid
target = test
start_lon = lon
curr_lat = lat
curr_lon  = start_lon
draw_b1=0
for ix in range(0,GRIDS):
    draw_b2 = 0
    for iy in range(0,GRIDS):
        points = [(curr_lat-step_lat,curr_lon-step_lon),(curr_lat+step_lat,curr_lon+step_lon)]
        if target[ix,iy] == FIRE:
            opa = 1
            folium.Rectangle(bounds=points,fill=True,color = 'black',fill_color = 'red',fill_opacity=opa,weight=1).add_to(lmap)
        elif target[ix,iy] == TREE:
            opa = 0.5
            folium.Rectangle(bounds=points,fill=True,color = 'black',fill_color = 'green',fill_opacity=opa,weight=1).add_to(lmap)
        
        draw_b2+=1
        curr_lon += step_lon*2
        
    draw_b1+=1
    curr_lat += step_lat*2
    curr_lon = start_lon

#plot data
data = data_y2019[data_y2019.acq_date.str.contains('2019-04-03')]
for _, row in data.iterrows():
    folium.CircleMarker(location=(row['latitude'], row['longitude']),
                        radius=6, fill_color='red', fill_opacity=1,
                        popup="<b>lat</b>: {} <b>lon</b>: {}".format(row['latitude'],row['longitude'])
                        ).add_to(lmap)
    points = [(row['latitude']-step_lat,row['longitude']-step_lon),(row['latitude']+step_lat,row['longitude']+step_lon)]
    #folium.Rectangle(bounds=points,fill=False,color = 'red',weight=1).add_to(lmap)
lmap

In [6]:
def iterate(X):
    """Iterate the forest according to the forest-fire rules."""
    # The boundary of the forest is always empty, so only consider cells
    # indexed from 1 to nx-2, 1 to ny-2
    EMPTY, TREE, FIRE = 0, 1, 2
    neighbourhood = ((-1,-1), (-1,0), (-1,1), (0,-1), (0, 1), (1,-1), (1,0), (1,1))
    nx, ny = 100, 100
    
    X1 = np.zeros((ny, nx))
    for ix in range(1,nx-1):
        for iy in range(1,ny-1):
            if X[iy,ix] == FIRE:
                X1[iy,ix] = EMPTY
            if X[iy,ix] == TREE:
                X1[iy,ix] = TREE
                for dx,dy in neighbourhood:
                    if X[iy+dy,ix+dx] == FIRE:
                        X1[iy,ix] = FIRE
                        break
    return X1

def forecastFire(old_hotspots,today_hotspots): #old_hotspots is hotspots each day in array [day1,day2,day3,...]
    hotspot_grid = []
    GRIDS = 101
    lands = np.ones((GRIDS,GRIDS))
    #loop to mark old hotspots as empty lands
    for day in old_hotspots:
        read_data = day
        #loop each data row
        for i,r in read_data.iterrows():
            #loop data grid
            for b1 in range(GRIDS):
                if lats[b1] - (lat_step/2) <= r['latitude'] < lats[b1] + (lat_step/2):
                    for b2 in range(GRIDS):
                        if lons[b2] - (lon_step/2 ) <= r['longitude'] < lons[b2] + (lon_step/2):
                            lands[b1,b2] = 0 # marks as empty land
                            #hotspots_counts[b1,b2] += 1
    #loop to mark today hotspots as fire
    for i,r in today_hotspots.iterrows():
            #loop data grid
            for b1 in range(GRIDS):
                if lats[b1] - (lat_step/2) <= r['latitude'] < lats[b1] + (lat_step/2):
                    for b2 in range(GRIDS):
                        if lons[b2] - (lon_step/2 ) <= r['longitude'] < lons[b2] + (lon_step/2):
                            lands[b1,b2] = 2 # marks as empty fire
    #append nearby fire risk
    predict_fire = iterate(lands)
    return predict_fire #101x101 array
#test data
day1 = april_data[april_data.acq_date.eq('2019-03-30')]
day2 = april_data[april_data.acq_date.eq('2019-03-31')]
day3 = april_data[april_data.acq_date.eq('2019-04-01')]
test_old_data = [day1,day2,day3]
test_today_data = april_data[april_data.acq_date.eq('2019-04-02')]
#run
test = forecastFire(test_old_data,test_today_data)

In [18]:
test[0][0]

0.0

In [21]:
def toDictOnlyFIREandEMPTY(dataGrid,date): #(101x101 array, date of data)
    CELLTYPE = ['EMPTY', 'TREE', 'FIRE']
    EMPTY, TREE, FIRE = 0, 1, 2
    pi = math.pi
    r_earth = 6371000.0 #m
    #start lat lon of grid (bottom left)
    lat = 17.779913 
    lon =  97.715363
    #grid distance
    dy2 = 350/2
    dx2 = 350/2
    step_lat =  (dy2 / r_earth) * (180 / pi)
    step_lon =  (dx2 / r_earth) * (180 / pi) / math.cos(lat * pi/180)
    #
    target = dataGrid
    start_lon = lon
    curr_lat = lat
    curr_lon  = start_lon
    draw_b1=0
    #to influx
    predict_points = []
    for ix in range(0,GRIDS):
        draw_b2 = 0
        for iy in range(0,GRIDS):
            points = [(curr_lat-step_lat,curr_lon-step_lon),(curr_lat+step_lat,curr_lon+step_lon)]
            #save data
            if target[ix,iy] != TREE:
                save_dict = {
                        'latitude' : lat + step_lat*2*ix,
                        'longitude' : lon + step_lon*2*iy,
                        'base_date' : unique_date[end_date],
                        'type': CELLTYPE[int(target[ix,iy])]
                }
                predict_points.append(save_dict)

        draw_b1+=1
        curr_lat += step_lat*2
        curr_lon = start_lon
    return predict_points #python dict only FIRE and EMPTY
test_date = '2019-04-02'
python_dict = toDictOnlyFIREandEMPTY(test,test_date)

NameError: name 'end_date' is not defined